In [67]:
import numpy as np
from numpy import random
import matplotlib.pyplot as plt
import matplotlib.colors as clr
%matplotlib osx
from matplotlib.animation import FFMpegWriter

(0.0, 1.0, 0.0, 1.0)

In [27]:
class Map:
    dirs = [(-1, 0), (1, 0), (0, -1), (0, 1)]
    def __init__(this, width, height):
        this.width = width
        this.height = height
        this.map = np.full((height, width), 0)
        this.doors = np.full((height, width, 4), False)
    def draw(this, ax):
        # generate an array for the walls
        wallT = 5
        walls = np.zeros((this.height*wallT, this.width*wallT))
        alphas = np.zeros((this.height*wallT, this.width*wallT))
        for i in range(this.height):
            for j in range(this.width):
                # entire room
                if not this.map[i, j]:
                    alphas[i*wallT:(i+1)*wallT, j*wallT:(j+1)*wallT] = 1
                    continue
                # walls
                alphas[i*wallT, j*wallT:(j+1)*wallT] = 1
                alphas[(i+1)*wallT-1, j*wallT:(j+1)*wallT] = 1
                alphas[i*wallT:(i+1)*wallT, j*wallT] = 1
                alphas[i*wallT:(i+1)*wallT, (j+1)*wallT-1] = 1
                # doors
                if this.doors[i, j, 0]:
                    alphas[i*wallT, j*wallT+2:(j+1)*wallT-2] = 0 # top
                if this.doors[i, j, 1]:
                    alphas[(i+1)*wallT-1, j*wallT+2:(j+1)*wallT-2] = 0 # bottom
                if this.doors[i, j, 2]:
                    alphas[i*wallT+2:(i+1)*wallT-2, j*wallT] = 0 # left
                if this.doors[i, j, 3]:
                    alphas[i*wallT+2:(i+1)*wallT-2, (j+1)*wallT-1] = 0 # right
        extent = (-0.5, this.width-0.5, this.height-0.5, -0.5)
        ax.imshow(this.map, cmap=clr.ListedColormap([[0,0,0,1],'xkcd:purple','xkcd:yellow','xkcd:green']),
                  norm=clr.BoundaryNorm([-0.5, 0.5, 1.5, 2.5, 3.5], 4), extent=extent)
        ax.imshow(walls, cmap=clr.ListedColormap([[0,0,0,1]]), alpha=alphas, extent=extent)
    def place_exit(this, rng, org_x, org_y, dist):
        #BFS to place at correct distance
        choices = []
        visited = np.zeros((this.height, this.width))
        queue = [(org_y, org_x, 0)]
        while len(queue) > 0 and queue[0][2] < dist + 1:
            cur = queue.pop(0)
            y = cur[0]
            x = cur[1]
            if not visited[y, x]:
                visited[y, x] = 1
                if cur[2] == dist:
                    choices.append(cur)

                valids = []
                if y - 1 >= 0 and this.doors[y, x, 0]:
                    valids.append((y-1, x, 0))
                if y + 1 < this.height and this.doors[y, x, 1]:
                    valids.append((y+1, x, 1))
                if x - 1 >= 0 and this.doors[y, x, 2]:
                    valids.append((y, x-1, 2))
                if x + 1 < this.width and this.doors[y, x, 3]:
                    valids.append((y, x+1, 3))
                for v in valids:
                    if not visited[v[0], v[1]]:
                        queue.append((v[0], v[1], cur[2] + 1))
        
        goal = rng.choice(choices)
        this.map[goal[0], goal[1]] = 3
    
    def Grid(width, height):
        map = Map(width, height)
        map.map = np.full((height, width), 1)
        map.doors = np.full((height, width, 4), True)
        for i in range(height):
            map.doors[i, 0, 2] = False
            map.doors[i, width-1, 3] = False
        for j in range(width):
            map.doors[0, j, 0] = False
            map.doors[height-1, j, 1] = False
        return map
    
    def DepthFirst(rng, width, height):
        map = Map(width, height)
        map.map = np.full((height, width), 1)
        visited = np.zeros((height, width))
        x, y = rng.integers(width), rng.integers(height)
        def visit(y, x):
            visited[y, x] = 1
            valids = []
            if y - 1 >= 0 and not visited[y-1, x]:
                valids.append((y-1, x, 0))
            if y + 1 < height and not visited[y+1, x]:
                valids.append((y+1, x, 1))
            if x - 1 >= 0 and not visited[y, x-1]:
                valids.append((y, x-1, 2))
            if x + 1 < width and not visited[y, x+1]:
                valids.append((y, x+1, 3))
            rng.shuffle(valids)
            for v in valids:
                if not visited[v[0], v[1]]:
                    map.doors[y, x, v[2]] = True
                    map.doors[v[0], v[1], v[2] ^ 1] = True
                    visit(v[0], v[1])
        visit(y, x)
        return map
    
    def RandOpen(rng, width, height):
        map = Map(width, height)
        map.map = np.full((height, width), 1)
        def ConnCheck():
            visited = np.zeros((height, width))
            def visit(y, x):
                visited[y, x] = 1
                valids = []
                if y - 1 >= 0 and map.doors[y, x, 0]:
                    valids.append((y-1, x, 0))
                if y + 1 < height and map.doors[y, x, 1]:
                    valids.append((y+1, x, 1))
                if x - 1 >= 0 and map.doors[y, x, 2]:
                    valids.append((y, x-1, 2))
                if x + 1 < width and map.doors[y, x, 3]:
                    valids.append((y, x+1, 3))
                for v in valids:
                    if not visited[v[0], v[1]]:
                        visit(v[0], v[1])
            visit(0, 0)
            return np.all(visited)
        
        walls = []
        for i in range(height * 2 - 1):
            if i % 2 == 0:
                walls.extend([(i, x) for x in range(width-1)])
            else:
                walls.extend([(i, x) for x in range(width)])
        rng.shuffle(walls)
        while not ConnCheck():
            wall = walls.pop()
            if wall[0] % 2 == 0:
                map.doors[wall[0] // 2, wall[1], 3] = True
                map.doors[wall[0] // 2, wall[1] + 1, 2] = True
            else:
                map.doors[wall[0] // 2, wall[1], 1] = True
                map.doors[wall[0] // 2 + 1, wall[1], 0] = True
        return map
            

In [9]:
# map gen tests
width = 10
height = 13
fig = plt.figure()
ax = fig.add_subplot(1, 1, 1)
rng = random.default_rng()

map = Map.RandOpen(rng, width, height)
map.draw(ax)
fig.show()

In [30]:
# random player test on grid
width = 10
height = 10
map = Map.Grid(width, height)
fig = plt.figure()
ax = fig.add_subplot(1, 1, 1)
rng = random.default_rng()

cur_x = rng.integers(width)
cur_y = rng.integers(height)
map.map[cur_y, cur_x] = 2
map.place_exit(rng, cur_x, cur_y, 10)
for it in range(1000):
    next_dirs = [Map.dirs[d] for d in range(4) if map.doors[cur_y, cur_x, d]]
    next_dir = rng.choice(next_dirs)
    cur_y += next_dir[0]
    cur_x += next_dir[1]
    if map.map[cur_y, cur_x] < 2:
        map.map[cur_y, cur_x] = 2
    ax.clear()
    map.draw(ax)
    ax.plot([cur_x], [cur_y], lw=0, marker="o")
    fig.show()
    plt.pause(0.1)
    if map.map[cur_y, cur_x] == 3:
        print(f"Exit found at iteration {it}.")
        break
print(f"Total rooms visited: {sum([1 for x in map.map.flatten() if x >= 2])}")

Exit found at iteration 115.
Total rooms visited: 54


In [72]:
class Player:
    def __init__(this, map, x, y):
        this.x = x
        this.y = y
        this.mem_locs = {}
        this.width = map.width
        this.height = map.height
        this.path_to = np.full((this.height, this.width), (-1, -1), dtype=(np.int32, 2))
        this.map = map
        this.cur_goal = (-1, -1)
        this.rng = random.default_rng()
        
    def visit(this):
        x = this.x
        y = this.y
        if this.map.map[y, x] == 3:
            return True
        if this.map.map[y, x] < 2:
            this.map.map[y, x] = 2
        #update paths for adjacent rooms
        if this.map.doors[y, x, 0]:
            if this.map.map[y-1, x] != 2:
                this.mem_locs[(y-1, x)] = 1
            this.path_to[y-1, x] = (y, x)
        if this.map.doors[y, x, 1]:
            if this.map.map[y+1, x] != 2:
                this.mem_locs[(y+1, x)] = 1
            this.path_to[y+1, x] = (y, x)
        if this.map.doors[y, x, 2]:
            if this.map.map[y, x-1] != 2:
                this.mem_locs[(y, x-1)] = 1
            this.path_to[y, x-1] = (y, x)
        if this.map.doors[y, x, 3]:
            if this.map.map[y, x+1] != 2:
                this.mem_locs[(y, x+1)] = 1
            this.path_to[y, x+1] = (y, x)
        return False
                    
    def perform_step(this):
        if this.visit():
            return True
        
        if np.all((this.y, this.x) == this.cur_goal):
            del this.mem_locs[tuple(this.cur_goal)]
            this.cur_goal = (-1, -1)
        
        if np.all(this.cur_goal == (-1, -1)):
            #choose new goal room randomly, closer rooms are more likely
            res, dist = this.find_dists()
            probs = np.array([1/x for x in dist])
            this.cur_goal = this.rng.choice(res, p=probs/probs.sum())
        
        #proceed towards goal
        tmp = this.cur_goal
        #print(f"tmp: {(tmp[1], tmp[0])}")
        while np.any(this.path_to[tmp[0], tmp[1]] != (this.y, this.x)):
            tmp = this.path_to[tmp[0], tmp[1]]
            #print(f"tmp: {(tmp[1], tmp[0])}")
        this.y, this.x = tmp
        return False
    
    def find_dists(this):
        res = list(this.mem_locs.keys())
        tmp = [x for x in res]
        dist = [0 for x in res]
        for i in range(len(res)):
            while tmp[i] != (this.y, this.x):
                dist[i] += 1
                tmp[i] = tuple(this.path_to[tmp[i][0], tmp[i][1]])
        return res, dist
    
    def draw(this, ax, show_goal=True):
        if show_goal:
            ax.plot([this.cur_goal[1]], [this.cur_goal[0]], lw=0, marker="x", mec="red", ms=10.0)
        ax.plot([this.x], [this.y], lw=0, marker="o", mfc="blue", mec="blue")

In [80]:
# player model test on grid
width = 10
height = 15
map = Map.Grid(width, height)
fig = plt.figure()
ax = fig.add_subplot(1, 1, 1)
rng = random.default_rng()
player = Player(map, rng.integers(width), rng.integers(height))
map.place_exit(rng, player.x, player.y, 15)
metadata = dict(title='Grid Trial', artist='Matplotlib')
writer = FFMpegWriter(fps=10, metadata=metadata)
ax.get_xaxis().set_visible(False)
ax.get_yaxis().set_visible(False)

map.draw(ax)
player.draw(ax, False)
fig.savefig('grid.png')

with writer.saving(fig, "grid.mp4", dpi=200):
    for it in range(1000):
        if player.perform_step():
            print(f"Exit found at iteration {it}.")
            break
        ax.clear()
        map.draw(ax)
        player.draw(ax)
        fig.show()
        plt.pause(0.01)
        writer.grab_frame()

Exit found at iteration 371.


In [77]:
# player model test on depth first
width = 10
height = 15
map = Map.DepthFirst(random.default_rng(), width, height)
fig = plt.figure()
ax = fig.add_subplot(1, 1, 1)
rng = random.default_rng()
player = Player(map, rng.integers(width), rng.integers(height))
map.place_exit(rng, player.x, player.y, 15)
metadata = dict(title='Depth First Trial', artist='Matplotlib')
writer = FFMpegWriter(fps=10, metadata=metadata)
ax.get_xaxis().set_visible(False)
ax.get_yaxis().set_visible(False)

map.draw(ax)
player.draw(ax, False)
fig.savefig('depth.png')

with writer.saving(fig, "depth.mp4", dpi=200):
    for it in range(1000):
        if player.perform_step():
            print(f"Exit found at iteration {it}.")
            break
        ax.clear()
        map.draw(ax)
        player.draw(ax)
        fig.show()
        plt.pause(0.01)
        writer.grab_frame()

Exit found at iteration 73.


In [93]:
# player model test on rand open
width = 10
height = 15
map = Map.RandOpen(random.default_rng(), width, height)
fig = plt.figure()
ax = fig.add_subplot(1, 1, 1)
rng = random.default_rng()
player = Player(map, rng.integers(width), rng.integers(height))
map.place_exit(rng, player.x, player.y, 15)
metadata = dict(title='Rand Open Trial', artist='Matplotlib')
writer = FFMpegWriter(fps=10, metadata=metadata)
ax.get_xaxis().set_visible(False)
ax.get_yaxis().set_visible(False)

map.draw(ax)
player.draw(ax, False)
fig.savefig('open.png')

with writer.saving(fig, "open.mp4", dpi=200):
    for it in range(1000):
        if player.perform_step():
            print(f"Exit found at iteration {it}.")
            break
        ax.clear()
        map.draw(ax)
        player.draw(ax)
        fig.show()
        plt.pause(0.01)
        writer.grab_frame()

Exit found at iteration 255.


In [95]:
#repeated simulations: should take 3~8 hours to run
width = 50
height = 50
dist = 40
times = [[], [], []]
visits = [[], [], []]
rng = random.default_rng()

print("Grid trials")
for trial in range(2000):
    if trial % 100 == 0:
        print(trial)
    map = Map.Grid(width, height)
    player = Player(map, rng.integers(width), rng.integers(height))
    map.place_exit(rng, player.x, player.y, 10)
    for it in range(25000):
        if player.perform_step():
            times[0].append(it)
            visits[0].append(np.count_nonzero(map.map >= 2))
            break

print("Rand open trials")
for trial in range(2000):
    if trial % 100 == 0:
        print(trial)
    map = Map.RandOpen(rng, width, height)
    player = Player(map, rng.integers(width), rng.integers(height))
    map.place_exit(rng, player.x, player.y, 10)
    for it in range(25000):
        if player.perform_step():
            times[1].append(it)
            visits[1].append(np.count_nonzero(map.map >= 2))
            break

print("Depth first trials")
for trial in range(2000):
    if trial % 100 == 0:
        print(trial)
    map = Map.DepthFirst(rng, width, height)
    player = Player(map, rng.integers(width), rng.integers(height))
    map.place_exit(rng, player.x, player.y, 10)
    for it in range(25000):
        if player.perform_step():
            times[2].append(it)
            visits[2].append(np.count_nonzero(map.map >= 2))
            break

Grid trials
0
100
200
300
400
500
600
700
800
900
1000
1100
1200
1300
1400
1500
1600
1700
1800
1900
Rand open trials
0
100
200
300
400
500
600
700
800
900
1000
1100
1200
1300
1400
1500
1600
1700
1800
1900
Depth first trials
0
100
200
300
400
500
600
700
800
900
1000
1100
1200
1300
1400
1500
1600
1700
1800
1900


In [135]:
plt.hist(times, bins=range(0, 5000, 200), label=['Grid', 'Random open', 'Depth first'])
plt.title('Exploration on 50x50 map with exit placed 40 moves away')
plt.xlabel('Moves taken')
plt.ylabel('Frequency')
plt.ylim([0, 300])
plt.legend()
plt.show()
plt.savefig('moves.png')

In [136]:
plt.hist([[x / (width * height) for x in l] for l in visits], bins=np.arange(0, 0.6, 0.05), label=['Grid', 'Random open', 'Depth first'])
plt.title('Exploration on 50x50 map with exit placed 40 moves away')
plt.xlabel('Percentage of rooms visited')
plt.ylabel('Frequency')
plt.ylim([0, 800])
plt.legend()
plt.show()
plt.savefig('exploration.png')